In [1]:
import pandas as pd
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
import numpy as np
import matplotlib.pyplot as plt
from imblearn.over_sampling import SMOTE
from xgboost import XGBClassifier, plot_importance
from lightgbm import LGBMClassifier
from catboost import CatBoostClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split, StratifiedKFold
from sklearn.metrics import accuracy_score, f1_score
import warnings
warnings.simplefilter('ignore')

- Submission_1 : Single XGB with random state 0 with SMOTE
- Submission_2 : Combination of 5 XGB and 5 Random Forest with Random state 0 with SMOTE
- Submission_3 : Combination of 5 Random Forest with Random state 0 with SMOTE
- Submission_4 : Submission 3 with Annual Income Dropped
- Submission_5 : Submission 2 with Annual Income Dropped
- Submission_6 : Submission 3 with Annual Income, Stay Duration of Current Residence and Tenure of Oldest Credit Line Dropped and random states 10 everywhere

In [2]:
train = pd.read_csv('TrainingData.csv')
test = pd.read_csv('testX.csv')

df = pd.concat([train, test], axis = 0)

df.shape

(130000, 53)

In [3]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 130000 entries, 0 to 46999
Data columns (total 53 columns):
 #   Column           Non-Null Count   Dtype  
---  ------           --------------   -----  
 0   application_key  130000 non-null  int64  
 1   mvar1            130000 non-null  object 
 2   mvar2            120787 non-null  float64
 3   mvar3            129171 non-null  float64
 4   mvar4            129171 non-null  float64
 5   mvar5            129171 non-null  float64
 6   mvar6            130000 non-null  object 
 7   mvar7            130000 non-null  object 
 8   mvar8            130000 non-null  object 
 9   mvar9            130000 non-null  object 
 10  mvar10           130000 non-null  object 
 11  mvar11           130000 non-null  object 
 12  mvar12           130000 non-null  object 
 13  mvar13           130000 non-null  object 
 14  mvar14           130000 non-null  int64  
 15  mvar15           130000 non-null  object 
 16  mvar16           130000 non-null  objec

In [4]:
columns = ['ID',
           'Credit Worthiness Score',
           'Number and Riskiness of Credit Enquiry',
           'Default Severity (Any Loan)',
           'Default Severity (Auto Loan)',
           'Default Severity (Education Loan)',
           'Min Cred Available (Revolving Credit Cards)',
           'Max Cred Available (Active Credit Lines)',
           'Max Cred Available (Active Revolving Credit Cards)',
           'Total Available Credit (Cards with 1 missed payment)',
           'Total Credit Available',
           'Dues Collected Post Default',
           'Total Amount Due (Active Cards)',
           'Credit Amount Paid (Prev Year)',
           'Annual Income',
           'Property Value',
           'Full Credit Utilisation (Revolving Credit Cards)',
           'Full Credit Utilisation (Credit Cards)',
           'Full Credit Utilisation (Credit Lines)',
           '>75 percent Credit Utilisation (Credit Cards)',
           '>75 percent Credit Utilisation (Credit Lines)',
           'Average Utilisation (Revolving Credit Cards)',
           'Average Utilisation Last 2 Years (All Credit Lines)',
           'Average Utilisation Last Year (All Credit Cards)',
           'Average Utilisation Last 6 Months with 1 Missed Payment (Credit Cards)',
           'Average Tenure (Active Revolving Credit Cards)',
           'Tenure of Oldest Active Credit Card',
           'Tenure of Oldest Active Revolving Credit Card',
           'Days Since Last Missed Payment',
           'Tenure of Oldest Credit Line',
           'Max Tenure (Auto Loans)',
           'Max Tenure (Education Loans)',
           'Sum of Tenures (Active Credit Cards)',
           'Stay Duration of Current Residence',
           'Credit Lines with 1 Missed Payment (Last 6 Months)',
           'Revolving Credit Cards with 1 Missed Payment (Last 2 Years)',
           'Active Credit Lines',
           'Credit Cards with >2Y Tenure',
           'Credit Lines activated Prev 2 Years',
           'Credit Lines with Current Delinquency',
           'Utilization on Active Education Loans',
           'Utilization on Active Auto Loans',
           'Financial Stress Index',
           'Credit Lines with No Missed Payments (Prev 2 Years)',
           'Ratio(Max Amount Due : Sum of Amounts Due)',
           'Mortgage Loans (With 2 Missed Payements)',
           'Auto Loans (With 2 Missed Payments)',
           'Type of Product',
           'Int Value for an Application',
           'Bucketized Credit Worthiness Score',
           'Compound of mvar49 and mvar48',
           'mvar51',
           'default_ind']

In [5]:
df.columns = columns

In [6]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 130000 entries, 0 to 46999
Data columns (total 53 columns):
 #   Column                                                                  Non-Null Count   Dtype  
---  ------                                                                  --------------   -----  
 0   ID                                                                      130000 non-null  int64  
 1   Credit Worthiness Score                                                 130000 non-null  object 
 2   Number and Riskiness of Credit Enquiry                                  120787 non-null  float64
 3   Default Severity (Any Loan)                                             129171 non-null  float64
 4   Default Severity (Auto Loan)                                            129171 non-null  float64
 5   Default Severity (Education Loan)                                       129171 non-null  float64
 6   Min Cred Available (Revolving Credit Cards)                          

### Feature Understanding (Explanations and Stuff to Look into)

- Auto Loans: Loans where Vehicles are kept as collateral
- Revolving Credit: You have a fixed amount that you can borrow in some fixed time frame. After that the amount you can borrow replenishes to the full amount. Although you will have a maximum limit. For example, you can borrow 100 rupees a month max and the overall limit on that credit line is 500 rupees. So if your overall borrowed amount is 460 rupees and for that month you havenn't borrowed anything so far, you will be able to borrow only 40 rupees even though the monthly limit is 100
- Difference between Credit Worthiness Score and its bucketized version?
- Difference in statistics between train and test (Need for Adverserial Validation?)

### Feature Ideas and Experiments
- Binary Variable for checking if the person has moved into current residence after issuing any credit lines
- Credit Amount Paid / Number of Credit Lines with No Missed Payments
- Max Cred Available vs Default Severity
- Separate modeling for 0 Default Severity vs Non-Zero Default Severity
- KNN Missing Values Fill In
- Property Value vs Annual Income (Some Indicator of whether or not a person spends too much for their Income)
- 75% utilisation / Full Utilisation

In [7]:
df.head(10)

ID Credit Worthiness Score  Number and Riskiness of Credit Enquiry  \
0  230032                    1696                                  1.6541   
1  230033                    1846                                  0.8095   
2  230034                    1745                                  0.4001   
3  230035                    1739                                  0.2193   
4  230036                    1787                                  0.0118   
5  230037                    1579                                     NaN   
6  230038                    1818                                  0.4001   
7  230039                      na                                     NaN   
8  230040                    1836                                  0.1358   
9  230041                    1839                                  0.1981   

   Default Severity (Any Loan)  Default Severity (Auto Loan)  \
0                        0.000                           0.0   
1                        0.000                           0.0   
2                        0.000                           0.0   
3                        0.000                           0.0   
4                        0.225                           0.0   
5                        3.502                           0.0   
6                        0.000                           0.0   
7                          NaN                           NaN   
8                        0.000                           0.0   
9                        0.000                           0.0   

   Default Severity (Education Loan)  \
0                                0.0   
1                                0.0   
2                                0.0   
3                                0.0   
4                                0.0   
5                                0.0   
6                                0.0   
7                                NaN   
8                                0.0   
9                                0.0   

  Min Cred Available (Revolving Credit Cards)  \
0                                           0   
1                                         102   
2                                     missing   
3                                        1982   
4                                        5451   
5                                     missing   
6                                     missing   
7                                     missing   
8                                         347   
9                                         793   

  Max Cred Available (Active Credit Lines)  \
0                                     6015   
1                                     7532   
2                                     2536   
3                                    26440   
4                                     5494   
5                                  missing   
6                                     1088   
7                                  missing   
8                                    38964   
9                                     6131   

  Max Cred Available (Active Revolving Credit Cards)  \
0                                                322   
1                                               3171   
2                                            missing   
3                                               4955   
4                                               5494   
5                                            missing   
6                                            missing   
7                                            missing   
8                                              17828   
9                                               6045   

  Total Available Credit (Cards with 1 missed payment) Total Credit Available  \
0                                              40369                    18414   
1                                              18234                    13664   
2                                            missing                     2536   
3                        

In [8]:
df.replace('missing', np.nan, inplace = True)
df.replace('na', np.nan, inplace = True)
df.replace('#VALUE!', np.nan, inplace = True)

In [9]:
df.head(10)

ID Credit Worthiness Score  Number and Riskiness of Credit Enquiry  \
0  230032                    1696                                  1.6541   
1  230033                    1846                                  0.8095   
2  230034                    1745                                  0.4001   
3  230035                    1739                                  0.2193   
4  230036                    1787                                  0.0118   
5  230037                    1579                                     NaN   
6  230038                    1818                                  0.4001   
7  230039                     NaN                                     NaN   
8  230040                    1836                                  0.1358   
9  230041                    1839                                  0.1981   

   Default Severity (Any Loan)  Default Severity (Auto Loan)  \
0                        0.000                           0.0   
1                        0.000                           0.0   
2                        0.000                           0.0   
3                        0.000                           0.0   
4                        0.225                           0.0   
5                        3.502                           0.0   
6                        0.000                           0.0   
7                          NaN                           NaN   
8                        0.000                           0.0   
9                        0.000                           0.0   

   Default Severity (Education Loan)  \
0                                0.0   
1                                0.0   
2                                0.0   
3                                0.0   
4                                0.0   
5                                0.0   
6                                0.0   
7                                NaN   
8                                0.0   
9                                0.0   

  Min Cred Available (Revolving Credit Cards)  \
0                                           0   
1                                         102   
2                                         NaN   
3                                        1982   
4                                        5451   
5                                         NaN   
6                                         NaN   
7                                         NaN   
8                                         347   
9                                         793   

  Max Cred Available (Active Credit Lines)  \
0                                     6015   
1                                     7532   
2                                     2536   
3                                    26440   
4                                     5494   
5                                      NaN   
6                                     1088   
7                                      NaN   
8                                    38964   
9                                     6131   

  Max Cred Available (Active Revolving Credit Cards)  \
0                                                322   
1                                               3171   
2                                                NaN   
3                                               4955   
4                                               5494   
5                                                NaN   
6                                                NaN   
7                                                NaN   
8                                              17828   
9                                               6045   

  Total Available Credit (Cards with 1 missed payment) Total Credit Available  \
0                                              40369                    18414   
1                                              18234                    13664   
2                                                NaN                     2536   
3                        

In [10]:
df.reset_index(drop = True, inplace = True)

In [11]:
def convert_to_int(entry):
    return float(entry)

for col in df.columns:
    if col not in ['Type of Product', 'default_ind']:
        df[col] = df[col].apply(convert_to_int)
        lower_percentile = 0
        higher_percentile = 0.9
        low, high = df[col].quantile([lower_percentile, higher_percentile])
        df[col][df[col] < low] = low
        df[col][df[col] > high] = high
        
    
df['Credit Worthiness Score'][0]

1696.0

In [12]:
df.fillna(-1, inplace = True)

In [13]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 130000 entries, 0 to 129999
Data columns (total 53 columns):
 #   Column                                                                  Non-Null Count   Dtype  
---  ------                                                                  --------------   -----  
 0   ID                                                                      130000 non-null  float64
 1   Credit Worthiness Score                                                 130000 non-null  float64
 2   Number and Riskiness of Credit Enquiry                                  130000 non-null  float64
 3   Default Severity (Any Loan)                                             130000 non-null  float64
 4   Default Severity (Auto Loan)                                            130000 non-null  float64
 5   Default Severity (Education Loan)                                       130000 non-null  float64
 6   Min Cred Available (Revolving Credit Cards)                         

In [14]:
df['default_ind'].value_counts()

 0.0    59145
-1.0    47000
 1.0    23855
Name: default_ind, dtype: int64

In [15]:
le = LabelEncoder()
df['Type of Product'] = le.fit_transform(df['Type of Product'])

In [16]:
import re
df = df.rename(columns = lambda x:re.sub('[^A-Za-z0-9_]+', '', x))

In [17]:
train = df.iloc[:83000, :]

X_data = train.drop(['ID', 'default_ind'], axis = 1)
y_data = train['default_ind']

#### Optimal Hyperparameter search

In [18]:
'''from sklearn.model_selection import GridSearchCV, RandomizedSearchCV
rf = RandomForestClassifier(random_state = 0, n_jobs = -1)

def clf_performance(classifier, model_name):
    print(model_name)
    print('Best Score: ' + str(classifier.best_score_))
    print('Best Parameters: ' + str(classifier.best_params_))
    
param_grid =  {'n_estimators': range(100, 200, 10), 
               'criterion':['gini','entropy'],
               'max_depth': [4, 6, 8, 10, 16, 20, 32, 50, None],
               'max_features': ['sqrt', 10, 50],
               'min_samples_leaf': [2,4,8,16,32],
               'min_samples_split': [4,8,16]}

sm = SMOTE(random_state = 0, k_neighbors = 3, n_jobs = -1)
X_Train, Y_Train = sm.fit_resample(X_data, y_data)

clf_rf = RandomizedSearchCV(rf, n_iter=1000, scoring = 'f1', param_distributions = param_grid,
                            cv = 5, verbose = 10, refit = True)

best_clf_rf = clf_rf.fit(X_Train, Y_Train)'''

"from sklearn.model_selection import GridSearchCV, RandomizedSearchCV\nrf = RandomForestClassifier(random_state = 0, n_jobs = -1)\n\ndef clf_performance(classifier, model_name):\n    print(model_name)\n    print('Best Score: ' + str(classifier.best_score_))\n    print('Best Parameters: ' + str(classifier.best_params_))\n    \nparam_grid =  {'n_estimators': range(100, 200, 10), \n               'criterion':['gini','entropy'],\n               'max_depth': [4, 6, 8, 10, 16, 20, 32, 50, None],\n               'max_features': ['sqrt', 10, 50],\n               'min_samples_leaf': [2,4,8,16,32],\n               'min_samples_split': [4,8,16]}\n\nsm = SMOTE(random_state = 0, k_neighbors = 3, n_jobs = -1)\nX_Train, Y_Train = sm.fit_resample(X_data, y_data)\n\nclf_rf = RandomizedSearchCV(rf, n_iter=1000, scoring = 'f1', param_distributions = param_grid,\n                            cv = 5, verbose = 10, refit = True)\n\nbest_clf_rf = clf_rf.fit(X_Train, Y_Train)"

In [19]:
#clf_performance(best_clf_rf,'Random Forest')

Best Parameters: {'n_estimators': 180, 'min_samples_split': 4, 'min_samples_leaf': 2, 'max_features': 'sqrt', 'max_depth': 32, 'criterion': 'gini'}

In [55]:
kfold = StratifiedKFold(random_state = 10, n_splits = 5, shuffle = True)
splits = kfold.split(X_data, y_data)

sm = SMOTE(random_state = 10, k_neighbors = 3, n_jobs = -1)

xgb_acc_scores = []
xgb_f1_scores = []
xgb_models = []

rf_acc_scores = []
rf_f1_scores = []
rf_models = []

i=1

for Train, Test in splits:
    X_Train, X_Test, Y_Train, Y_Test = X_data.iloc[Train], X_data.iloc[Test], y_data.iloc[Train], y_data.iloc[Test]
    
    xgb = LGBMClassifier(n_estimators = 10000, max_depth = 8, n_jobs = -1, min_child_samples=32,
                        learning_rate = 0.01, random_state = 10, early_stopping_round = 1000,
                        scale_pos_weight = 59145/23855)
    
    #rf = RandomForestClassifier(n_estimators = 130, max_depth=8, oob_score = True,
    #                            class_weight = 'balanced_subsample', n_jobs=-1,
    #                            random_state=10)

    X_Train, Y_Train = sm.fit_resample(X_Train, Y_Train)
    
    xgb.fit(X_Train, Y_Train, eval_set = [(X_Train, Y_Train), (X_Test, Y_Test)], verbose = True)
    
    pred = xgb.predict(X_Test)
    
    xgb_f1_scores.append(f1_score(Y_Test, pred))
    xgb_acc_scores.append(accuracy_score(Y_Test, pred)*100)
    xgb_models.append(xgb)
    '''
    rf.fit(X_Train, Y_Train)
    
    pred = rf.predict(X_Test)
    
    rf_f1_scores.append(f1_score(Y_Test, pred))
    rf_acc_scores.append(accuracy_score(Y_Test, pred)*100)
    rf_models.append(rf)
    '''
    print("Iteration {} Completed".format(i))
    i+=1

[1]	training's binary_logloss: 0.690055	valid_1's binary_logloss: 0.692
[2]	training's binary_logloss: 0.687014	valid_1's binary_logloss: 0.690875
[3]	training's binary_logloss: 0.684036	valid_1's binary_logloss: 0.689773
[4]	training's binary_logloss: 0.681128	valid_1's binary_logloss: 0.688718
[5]	training's binary_logloss: 0.678214	valid_1's binary_logloss: 0.687622
[6]	training's binary_logloss: 0.675403	valid_1's binary_logloss: 0.686605
[7]	training's binary_logloss: 0.672595	valid_1's binary_logloss: 0.685558
[8]	training's binary_logloss: 0.669897	valid_1's binary_logloss: 0.684589
[9]	training's binary_logloss: 0.667213	valid_1's binary_logloss: 0.683601
[10]	training's binary_logloss: 0.664619	valid_1's binary_logloss: 0.682695
[11]	training's binary_logloss: 0.662061	valid_1's binary_logloss: 0.681758
[12]	training's binary_logloss: 0.659522	valid_1's binary_logloss: 0.680842
[13]	training's binary_logloss: 0.657063	valid_1's binary_logloss: 0.679981
[14]	training's binary_l

[120]	training's binary_logloss: 0.524584	valid_1's binary_logloss: 0.640453
[121]	training's binary_logloss: 0.523932	valid_1's binary_logloss: 0.64023
[122]	training's binary_logloss: 0.523364	valid_1's binary_logloss: 0.64011
[123]	training's binary_logloss: 0.52279	valid_1's binary_logloss: 0.640002
[124]	training's binary_logloss: 0.522195	valid_1's binary_logloss: 0.63986
[125]	training's binary_logloss: 0.521521	valid_1's binary_logloss: 0.63963
[126]	training's binary_logloss: 0.520796	valid_1's binary_logloss: 0.639349
[127]	training's binary_logloss: 0.520219	valid_1's binary_logloss: 0.639213
[128]	training's binary_logloss: 0.519631	valid_1's binary_logloss: 0.639077
[129]	training's binary_logloss: 0.518934	valid_1's binary_logloss: 0.638813
[130]	training's binary_logloss: 0.518358	valid_1's binary_logloss: 0.63868
[131]	training's binary_logloss: 0.517824	valid_1's binary_logloss: 0.638558
[132]	training's binary_logloss: 0.517254	valid_1's binary_logloss: 0.638412
[133]

[241]	training's binary_logloss: 0.470884	valid_1's binary_logloss: 0.620613
[242]	training's binary_logloss: 0.470573	valid_1's binary_logloss: 0.620448
[243]	training's binary_logloss: 0.470229	valid_1's binary_logloss: 0.620244
[244]	training's binary_logloss: 0.46991	valid_1's binary_logloss: 0.620077
[245]	training's binary_logloss: 0.469533	valid_1's binary_logloss: 0.619869
[246]	training's binary_logloss: 0.469223	valid_1's binary_logloss: 0.619697
[247]	training's binary_logloss: 0.468858	valid_1's binary_logloss: 0.619495
[248]	training's binary_logloss: 0.468544	valid_1's binary_logloss: 0.619327
[249]	training's binary_logloss: 0.468184	valid_1's binary_logloss: 0.619122
[250]	training's binary_logloss: 0.467885	valid_1's binary_logloss: 0.618953
[251]	training's binary_logloss: 0.467553	valid_1's binary_logloss: 0.618776
[252]	training's binary_logloss: 0.467223	valid_1's binary_logloss: 0.618577
[253]	training's binary_logloss: 0.466914	valid_1's binary_logloss: 0.61841
[

[356]	training's binary_logloss: 0.438846	valid_1's binary_logloss: 0.600711
[357]	training's binary_logloss: 0.438641	valid_1's binary_logloss: 0.600567
[358]	training's binary_logloss: 0.438463	valid_1's binary_logloss: 0.600448
[359]	training's binary_logloss: 0.438234	valid_1's binary_logloss: 0.600287
[360]	training's binary_logloss: 0.438087	valid_1's binary_logloss: 0.600206
[361]	training's binary_logloss: 0.437909	valid_1's binary_logloss: 0.600094
[362]	training's binary_logloss: 0.437686	valid_1's binary_logloss: 0.599934
[363]	training's binary_logloss: 0.43749	valid_1's binary_logloss: 0.599797
[364]	training's binary_logloss: 0.437279	valid_1's binary_logloss: 0.599653
[365]	training's binary_logloss: 0.43711	valid_1's binary_logloss: 0.599541
[366]	training's binary_logloss: 0.43689	valid_1's binary_logloss: 0.599389
[367]	training's binary_logloss: 0.436671	valid_1's binary_logloss: 0.599239
[368]	training's binary_logloss: 0.436475	valid_1's binary_logloss: 0.59911
[36

[483]	training's binary_logloss: 0.418581	valid_1's binary_logloss: 0.58694
[484]	training's binary_logloss: 0.418442	valid_1's binary_logloss: 0.586836
[485]	training's binary_logloss: 0.418328	valid_1's binary_logloss: 0.586764
[486]	training's binary_logloss: 0.41824	valid_1's binary_logloss: 0.586706
[487]	training's binary_logloss: 0.418052	valid_1's binary_logloss: 0.586563
[488]	training's binary_logloss: 0.417966	valid_1's binary_logloss: 0.586515
[489]	training's binary_logloss: 0.417832	valid_1's binary_logloss: 0.586415
[490]	training's binary_logloss: 0.417638	valid_1's binary_logloss: 0.586275
[491]	training's binary_logloss: 0.417526	valid_1's binary_logloss: 0.586208
[492]	training's binary_logloss: 0.417468	valid_1's binary_logloss: 0.586189
[493]	training's binary_logloss: 0.417391	valid_1's binary_logloss: 0.586155
[494]	training's binary_logloss: 0.417202	valid_1's binary_logloss: 0.586011
[495]	training's binary_logloss: 0.41707	valid_1's binary_logloss: 0.585911
[4

...

[9445]	training's binary_logloss: 0.225082	valid_1's binary_logloss: 0.528319
[9446]	training's binary_logloss: 0.22507	valid_1's binary_logloss: 0.528321
[9447]	training's binary_logloss: 0.225056	valid_1's binary_logloss: 0.528315
[9448]	training's binary_logloss: 0.225046	valid_1's binary_logloss: 0.528316
[9449]	training's binary_logloss: 0.225035	valid_1's binary_logloss: 0.528319
[9450]	training's binary_logloss: 0.225021	valid_1's binary_logloss: 0.528316
[9451]	training's binary_logloss: 0.225007	valid_1's binary_logloss: 0.528316
[9452]	training's binary_logloss: 0.224995	valid_1's binary_logloss: 0.528308
[9453]	training's binary_logloss: 0.224984	valid_1's binary_logloss: 0.52831
[9454]	training's binary_logloss: 0.224972	valid_1's binary_logloss: 0.52831
[9455]	training's binary_logloss: 0.224958	valid_1's binary_logloss: 0.52831
[9456]	training's binary_logloss: 0.22495	valid_1's binary_logloss: 0.528314
[9457]	training's binary_logloss: 0.224936	valid_1's binary_logloss: 

[9577]	training's binary_logloss: 0.223473	valid_1's binary_logloss: 0.528127
[9578]	training's binary_logloss: 0.22346	valid_1's binary_logloss: 0.528134
[9579]	training's binary_logloss: 0.223447	valid_1's binary_logloss: 0.528134
[9580]	training's binary_logloss: 0.223436	valid_1's binary_logloss: 0.528129
[9581]	training's binary_logloss: 0.223421	valid_1's binary_logloss: 0.528124
[9582]	training's binary_logloss: 0.223407	valid_1's binary_logloss: 0.528119
[9583]	training's binary_logloss: 0.223397	valid_1's binary_logloss: 0.528116
[9584]	training's binary_logloss: 0.223383	valid_1's binary_logloss: 0.52811
[9585]	training's binary_logloss: 0.223368	valid_1's binary_logloss: 0.528112
[9586]	training's binary_logloss: 0.223357	valid_1's binary_logloss: 0.528111
[9587]	training's binary_logloss: 0.223343	valid_1's binary_logloss: 0.528109
[9588]	training's binary_logloss: 0.22333	valid_1's binary_logloss: 0.528115
[9589]	training's binary_logloss: 0.22332	valid_1's binary_logloss:

[9710]	training's binary_logloss: 0.221837	valid_1's binary_logloss: 0.527929
[9711]	training's binary_logloss: 0.221823	valid_1's binary_logloss: 0.527925
[9712]	training's binary_logloss: 0.221809	valid_1's binary_logloss: 0.527916
[9713]	training's binary_logloss: 0.221799	valid_1's binary_logloss: 0.527917
[9714]	training's binary_logloss: 0.221786	valid_1's binary_logloss: 0.527916
[9715]	training's binary_logloss: 0.221774	valid_1's binary_logloss: 0.527918
[9716]	training's binary_logloss: 0.221759	valid_1's binary_logloss: 0.527919
[9717]	training's binary_logloss: 0.221747	valid_1's binary_logloss: 0.527924
[9718]	training's binary_logloss: 0.221735	valid_1's binary_logloss: 0.527924
[9719]	training's binary_logloss: 0.221721	valid_1's binary_logloss: 0.527914
[9720]	training's binary_logloss: 0.221706	valid_1's binary_logloss: 0.527907
[9721]	training's binary_logloss: 0.221696	valid_1's binary_logloss: 0.527911
[9722]	training's binary_logloss: 0.221688	valid_1's binary_logl

[9842]	training's binary_logloss: 0.220228	valid_1's binary_logloss: 0.527817
[9843]	training's binary_logloss: 0.220215	valid_1's binary_logloss: 0.527815
[9844]	training's binary_logloss: 0.220204	valid_1's binary_logloss: 0.52781
[9845]	training's binary_logloss: 0.220191	valid_1's binary_logloss: 0.527813
[9846]	training's binary_logloss: 0.220182	valid_1's binary_logloss: 0.527814
[9847]	training's binary_logloss: 0.220169	valid_1's binary_logloss: 0.527815
[9848]	training's binary_logloss: 0.220161	valid_1's binary_logloss: 0.527819
[9849]	training's binary_logloss: 0.220146	valid_1's binary_logloss: 0.527817
[9850]	training's binary_logloss: 0.220134	valid_1's binary_logloss: 0.527818
[9851]	training's binary_logloss: 0.220123	valid_1's binary_logloss: 0.527811
[9852]	training's binary_logloss: 0.220109	valid_1's binary_logloss: 0.527809
[9853]	training's binary_logloss: 0.220097	valid_1's binary_logloss: 0.527807
[9854]	training's binary_logloss: 0.220081	valid_1's binary_loglo

[9974]	training's binary_logloss: 0.218668	valid_1's binary_logloss: 0.527676
[9975]	training's binary_logloss: 0.218654	valid_1's binary_logloss: 0.527678
[9976]	training's binary_logloss: 0.218644	valid_1's binary_logloss: 0.527676
[9977]	training's binary_logloss: 0.218632	valid_1's binary_logloss: 0.527676
[9978]	training's binary_logloss: 0.218621	valid_1's binary_logloss: 0.527675
[9979]	training's binary_logloss: 0.218608	valid_1's binary_logloss: 0.527675
[9980]	training's binary_logloss: 0.218597	valid_1's binary_logloss: 0.527673
[9981]	training's binary_logloss: 0.218589	valid_1's binary_logloss: 0.52767
[9982]	training's binary_logloss: 0.218577	valid_1's binary_logloss: 0.527666
[9983]	training's binary_logloss: 0.218565	valid_1's binary_logloss: 0.527664
[9984]	training's binary_logloss: 0.218554	valid_1's binary_logloss: 0.527666
[9985]	training's binary_logloss: 0.218545	valid_1's binary_logloss: 0.527665
[9986]	training's binary_logloss: 0.218534	valid_1's binary_loglo

In [56]:
print("XGB F1 Score: ", sum(xgb_f1_scores)/len(xgb_f1_scores))
print("XGB Accuracy: ", sum(xgb_acc_scores)/len(xgb_acc_scores), "%")
#print("RF F1 Score: ", sum(rf_f1_scores)/len(rf_f1_scores))
#print("RF Accuracy: ", sum(rf_acc_scores)/len(rf_acc_scores), "%")

XGB F1 Score:  0.5807803176359002
XGB Accuracy:  74.1843373493976 %


In [ ]:
'''
0.5891452
xgb = LGBMClassifier(n_estimators = 2000, max_depth = 8, n_jobs = -1,
                        learning_rate = 0.01, random_state = 0, early_stopping_round = 200,
                        scale_pos_weight = 59145/23855)

model = xgb_models[0]

plt.figure(figsize = (10,10))
plot_importance(model, max_num_features = 5)
plt.show()'''

In [109]:
test = df.iloc[83000:, :]
test = test.drop(['ID', 'default_ind'], axis = 1)

In [110]:
preds = np.argmax(#xgb_models[0].predict_proba(test) +
                  #xgb_models[1].predict_proba(test) +
                  #xgb_models[2].predict_proba(test) +
                  #xgb_models[3].predict_proba(test) +
                  #xgb_models[4].predict_proba(test) +
                  rf_models[0].predict_proba(test) +
                  rf_models[1].predict_proba(test) +
                  rf_models[2].predict_proba(test) +
                  rf_models[3].predict_proba(test) +
                  rf_models[4].predict_proba(test), axis = 1)

In [111]:
#preds = best_clf_rf.best_estimator_.predict(test)

In [112]:
sample = pd.read_csv('submission.csv', header = None)
sample.head()

0  1
0  578069  0
1  578070  1
2  578071  1
3  578072  1
4  578073  0

In [113]:
sample[1] = preds
sample.head()

0  1
0  578069  0
1  578070  0
2  578071  0
3  578072  1
4  578073  0

In [114]:
sample[1].value_counts()

0    27287
1    19713
Name: 1, dtype: int64

In [115]:
#sample.to_csv('Submissions/ThirdDegreeBurn_11.csv', index = False, header=False)